<center><h2>M1 MMA - Optimisation</h2><h3>TP2 : descente de gradient à pas optimal</h3></center>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

<h3>I) Algorithme de descente de gradient à pas optimal</h3>

On considère la fonction suivante définie pour tout $x=(x_0,x_1)\in\mathbb R^2$ par :
$$
f(x) = x_0^2 + 2 x_1^2 + x_0x_1 + x_0 - x_1 + 20.
$$

<b>0) Montrer que $f$ est une fonctionnelle quadratique et qu'elle admet un unique minimum global.</b>

<b>1) Ecrire en Python la fonction $f$, son gradient ainsi que la matrice symétrique $A$ et le vecteur $b$ tels que
$$
f(x) = \frac12 \langle Ax, x\rangle - \langle b, x \rangle + c.
$$
</b>

attention si implémentation de f via calcul vectoriel, bug avec la représentation graphique utilisant meshgrid. Il faut ici faire une implémentation de f accédant aux coefficients. On a donc pas besoin ici de la matrice A et du vecteur b.

<b>2) Tracer les lignes de niveau de $f$ sur $[-5,5]\times[-5,5]$.</b>

<b>3) Ecrire une fonction $\mbox{descente_gradient_pas_optimal}$, qui prend en argument un point de départ $x^{(0)}$, la matrice $A$, le vecteur $b$ et une tolérance $\varepsilon$, qui représente l'algorithme de descente de gradient à pas optimal. Cette fonction renverra le point final obtenu ainsi que la liste des itérés.</b>

<b>4) On prendra $x^{(0)}=(4,-4)$. Superposer la trajectoire donnée par l'algorithme au graphe des lignes de niveau de $f$. Commenter la trajectoire.</b>

<b>5) Illustrer la convergence de l'algorithme. On pourra represénter les valeurs successives de la fonction objective.</b>

<b>6) Observer votre code : quelle est l'opération la plus couteuse numériquement à chaque passage dans la boucle ? Quelle en est la complexité ? Combien de fois est-elle présente dans votre code ?</b>

<b>7) Montrer qu'il est possible d'adapter l'implémentation de sorte qu'une seule de ces opérations est nécessaire.</b>

<h3>II) Applications au débruitage d'images</h3>

In [ ]:
def ps(x, y):
    # produit scalaire entre x et y, qui peuvent être des vecteurs ou des matrices.
    return np.sum(x*y)

On charge l'image sur laquelle on va travailler

Récupérer l'image à l'adresse : https://qdenoyelle.github.io/M1_Optim/TP/hameau.png et la placer dans le dossier où le TP se situe.

In [ ]:
plt.figure(figsize = (8, 6))
img_original = plt.imread("hameau.png").astype(float) # chargement de l'image
img_original = sum([img_original[:, :, i] for i in range(2)]) # on transforme l'image en noir et blanc
img_original = 1/(np.max(img_original)-np.min(img_original))*(img_original - np.min(img_original))
plt.imshow(img_original, cmap = 'gray') # affichage de l'image
plt.show()

On va traiter l'image comme une matrice dont les coefficients sont le niveau de gris des pixels.

In [ ]:
n, m = img_original.shape # on récupère le nombre de ligne et de colonnes.
print("Nombre de lignes : ", n)
print("Nombre de colonnes : ", m)

On va maintenant dégrader l'image par un bruit additif gaussien (en pratique on aurait uniquement accès à l'image bruitée, ici on cré "artificiellement" le bruit).

In [ ]:
bruit = .2 * np.random.randn(n, m) # bruit gaussien qui va être appliqué sur l'image
img_bruite = img_original + bruit # on bruite additivement l'image

<b>1) Afficher l'image bruitée.</b>

Dans la suite les images seront vues comme des tableaux de valeurs (chaque pixel est un nombre représentant le niveau de gris), c'est à dire des matrices à $n$ lignes et $m$ colonnes.

On va maintenant chercher à débruiter l'image ci-dessus (i.e. diminuer l'impact du bruit). La méthode adoptée va consister à résoudre le problème d'optimisation suivant
$$
\min_{x\in\mathcal{M}_{n,m}(\mathbb{R})} F(x),
$$
où
$$
F(x) = \frac12 \sum_{i=1}^n\sum_{j=1}^m (x_{i,j} - y_{i,j})^2 + \frac{\lambda}2 \sum_{i=1}^{n-1}\sum_{j=1}^m (x_{i+1,j} - x_{i,j})^2 + \frac{\lambda}2 \sum_{i=1}^{n}\sum_{j=1}^{m-1} (x_{i,j+1} - x_{i,j})^2.
$$
$y\in\mathcal{M}_{n,m}(\mathbb{R})$ est l'image bruitée (la donnée du problème) et $\lambda>0$ une constante.

<b>2) Quel est la dimension de ce problème d'optimisation ?</b>

<b>3) Interpréter $F$.</b>

<b>4) Démontrer que $F$ peut s'écrire sous la forme
$$
\forall x\in\mathcal{M}_{n,m}(\mathbb{R}), \quad F(x) = \frac12 \langle \mathcal{A}(x), x \rangle - \langle b, x\rangle + c,
$$
où
<ul>
<li>$\langle \cdot, \cdot \rangle$ est le produit scalaire canonique sur l'espace $\mathcal{M}_{n,m}(\mathbb{R})$, c'est-à-dire $\langle x, x' \rangle = \mbox{Tr}(x^Tx') = \sum_{i,j} x_{i,j}x'_{i,j}$,</li>
<li>$\mathcal{A}:\mathcal{M}_{n,m}(\mathbb{R})\to\mathcal{M}_{n,m}(\mathbb{R})$ est un opérateur linéaire,</li>
<li>$b\in\mathcal{M}_{n,m}(\mathbb{R})$ et $c \in \mathbb R$.</li>
</ul>

On pourra introduire les matrices $L\in\mathcal{M}_{n, n}(\mathbb{R})$ avec des $-1$ sur la diagonale, et des $1$ sur la sur-diagonale, et $L_{n, n}=0$, et $C\in\mathcal{M}_{m, m}(\mathbb{R})$ la matrice avec des $-1$ sur la diagonale, $1$ sur la sous-diagonale et $C_{m, m}=0$</b>.

<b>5) Démontrer que $\mathcal{A}$ est un endomorphisme symétrique, c'est-à-dire pour tous $x,x'\in\mathcal{M}_{m,n}(\mathbb{R})$, $\langle \mathcal{A}(x), x' \rangle = \langle x, \mathcal{A}(x') \rangle$, puis que $\mathcal{A}$ est définie positive, c'est-à-dire pour tous $x\neq0$, $\langle \mathcal{A}(x), x \rangle >0$.</b>

<b>6) Justifier que $F$ admet un unique minimum global.</b>

<b>7) Ecrire une fonction $\mbox{opA}$ qui prend comme argument $x$ et qui renvoie $\mathcal{A}(x)$. On pourra commencer par créer les deux matrices $L$ et $C$ à l'aide de la commande np.eye (penser à regarder l'effet par exemple de np.eye(4) et np.eye(4, k = 1)).</b>

<b>8) Ecrire une fonction $\mbox{fobj}$ qui renvoient pour une matrice $x$, la valeur $F(x)$ du problème d'optimisation considéré.</b>

<b>9) Reprendre la fonction effectuant la descente de gradient à pas optimal et l'adapter pour qu'elle deviennent opérante dans le cas étudié ici : $A$ n'est plus une matrice mais un opérateur linéaire (donc une fonction), le produit scalaire est celui entre les matrices.</b>

<b>10) Utiliser l'algorithme pour le résoudre le problème d'optimisation. On prendra pour l'instant $\lambda = 5$. Afficher l'image débruitée.</b>

<b>11) Illustrer la convergence de la méthode.</b>

<b>12) Discuter de l'influence de $\lambda$.</b>